In [1]:
import spacy_dbpedia_spotlight
import spacy
import pandas as pd
import time
import requests
from difflib import SequenceMatcher
from tqdm import tqdm
import csv
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import train_test_split

In [2]:
#Read TextCorpus for Annotation
df = pd.read_pickle('data/textCorpusCleanedV1.0')
df.shape

(3210, 2)

In [3]:
#df = df.head(25).copy()
#df.shape

In [4]:
#spotlight = spacy_dbpedia_spotlight.create('en') # superseded from old gpu server spacy_dbpedia_spotlight.load('en') 

spotlight = spacy.blank('en')
#spotlight.add_pipe('dbpedia_spotlight', config={'confidence': 0.25}) #free internet API
spotlight.add_pipe('dbpedia_spotlight', config={'confidence': 0.25, 'dbpedia_rest_endpoint': 'http://192.168.78.101:9090/dbpedia/en/rest'}) # our own DBPedia Service

#sentencizer = spacy.load('en_core_web_sm')

In [5]:
#Split sentences to rows to be able to distinguish sentences with multiple or no entities.
def split_sents(text):
    entities =[]
    #Due to long texts, we gotta split them for the requests..
    #doc = sentencizer(text)
    #sentences = [clean_text(sent.text) for sent in doc.sents]
    
    sentences = text.split('.')
    sentences = [sent for sent in sentences]
    
    for i, sent in enumerate(sentences):
        sentences[i] = sentences[i].replace(',', '')
        sentences[i] = sentences[i].replace(',', '')
        sentences[i] = sentences[i].replace('"', '')
        sentences[i] = sentences[i].replace('.', ' ')
        sentences[i] = sentences[i].replace('(', '')
        sentences[i] = sentences[i].replace(')', '')
        sentences[i] = sentences[i].strip()
    
    return sentences

df["text"] = df["text"].apply(lambda row: split_sents(row) )
df = df.explode("text")
df.reset_index(inplace=True)

In [6]:
df.text[0]

'gamma-Hydroxybutyric acid or -Hydroxybutyric acid GHB also known as 4-hydroxybutanoic acid is a naturally occurring neurotransmitter and a psychoactive drug'

In [7]:
#Annotation method
def annotate_text(text):
    entities =[]
    #Due to long texts, we gotta split them for the requests..
    #doc = sentencizer(text)
    #sentences = [sent.string.strip() for sent in doc.sents]
    
    #for sentence in sentences:
    try:
        doc2 = spotlight(text)
        entities.extend([(ent.text, ent.kb_id_) for ent in doc2.ents])
    except Exception as e:
        print('Error ', e, ' at ', text) #sentence)
    #entities =  [(ent.text, ent.label_, ent.kb_id_) for ent in doc.ents]
    
    
    return list(dict.fromkeys(entities)) #Return only unique entries..



In [8]:
#%%time
tqdm.pandas()

df['entities'] = df['text'].progress_apply(lambda text: annotate_text(text))

  0%|          | 17/202476 [00:00<1:20:08, 42.10it/s]

Error  [E1010] Unable to set entity information for token 27 which is included in more than one span in entities, blocked, missing or outside.  at  GHB is used for medical purposes in the treatment of narcolepsy and more rarely alcoholism although its use for alcoholism is not supported by evidence from randomized controlled trials


  0%|          | 38/202476 [00:00<1:19:49, 42.27it/s]

23 36 {'@URI': 'http://dbpedia.org/resource/Gamma-Butyrolactone', '@support': '81', '@types': 'Wikidata:Q11173,DUL:ChemicalObject,DBpedia:ChemicalSubstance,DBpedia:ChemicalCompound', '@surfaceForm': 'butyrolactone', '@offset': '23', '@similarityScore': '1.0', '@percentageOfSecondRank': '0.0'}
Error  [E1010] Unable to set entity information for token 7 which is included in more than one span in entities, blocked, missing or outside.  at  A 2006 report commissioned by a UK parliamentary committee found the use of GHB to be less dangerous than tobacco and alcohol in physical harm dependence and social harms


  0%|          | 70/202476 [00:01<1:27:52, 38.39it/s]

...

Error  [E1010] Unable to set entity information for token 1 which is included in more than one span in entities, blocked, missing or outside.  at  The International Journal of Neuropsychopharmacology
0 3 {'@URI': 'http://dbpedia.org/resource/Digital_object_identifier', '@support': '1048', '@types': '', '@surfaceForm': 'doi', '@offset': '0', '@similarityScore': '0.999885313701591', '@percentageOfSecondRank': '1.1469944716172168E-4'}


100%|█████████▉| 202445/202476 [1:27:53<00:00, 134.38it/s]

0 3 {'@URI': 'http://dbpedia.org/resource/Digital_object_identifier', '@support': '1048', '@types': '', '@surfaceForm': 'doi', '@offset': '0', '@similarityScore': '0.999885313701591', '@percentageOfSecondRank': '1.1469944716172168E-4'}
0 3 {'@URI': 'http://dbpedia.org/resource/Digital_object_identifier', '@support': '1048', '@types': '', '@surfaceForm': 'doi', '@offset': '0', '@similarityScore': '0.999885313701591', '@percentageOfSecondRank': '1.1469944716172168E-4'}


100%|██████████| 202476/202476 [1:27:53<00:00, 38.39it/s] 

Error  [E1010] Unable to set entity information for token 118 which is included in more than one span in entities, blocked, missing or outside.  at  Paperback: App 200 pages -  Publisher: The Beckley Foundation Press and Oxford University Press June 2010 ISBN 978-0-19-958982-1  Hoffmanns Elixir: LSD and the new Eleusis - Talks & Essays by Albert Hofmann and othersEdited by Amanda Feilding -  Publisher: Beckley Foundation Press 2010 ISBN 978-0-9548054-9-4  Non-Invasive Evaluation of Human Brain Fluid Dynamics and Skull Biomechanics in Relation to Cognitive FunctioningAuthors: Yuri Moskalenko Amanda Feilding and Peter Halvorson -  Publisher: Beckley Foundation Press 2010 ISBN 978-1-907072-01-7 Drugs and the Brain Magdalen College Oxford 2002
194 201 {'@URI': 'http://dbpedia.org/resource/Control_theory', '@support': '1548', '@types': '', '@surfaceForm': 'Control', '@offset': '194', '@similarityScore': '0.8877006607729865', '@percentageOfSecondRank': '0.10689067146976806'}


In [9]:
#Get a list of all entities contained
all_entity_list = df.entities.sum()
#Remove duplicates
unique_entities = list(dict.fromkeys(all_entity_list))

print(len(unique_entities), ' entities need to be matched')

132626  entities need to be matched


In [10]:
unique_entities

[('gamma-Hydroxybutyric acid',
  'http://dbpedia.org/resource/Gamma-Hydroxybutyric_acid'),
 ('acid', 'http://dbpedia.org/resource/Lysergic_acid_diethylamide'),
 ('GHB', 'http://dbpedia.org/resource/Gamma-Hydroxybutyric_acid'),
 ('naturally', 'http://dbpedia.org/resource/Natural_product'),
 ('neurotransmitter', 'http://dbpedia.org/resource/Neurotransmitter'),
 ('psychoactive drug', 'http://dbpedia.org/resource/Psychoactive_drug'),
 ('It', 'http://dbpedia.org/resource/Schizophrenia'),
 ('precursor', 'http://dbpedia.org/resource/Protein_precursor'),
 ('GABA', 'http://dbpedia.org/resource/Gamma-Aminobutyric_acid'),
 ('glutamate', 'http://dbpedia.org/resource/Glutamic_acid'),
 ('glycine', 'http://dbpedia.org/resource/Glycine'),
 ('brain', 'http://dbpedia.org/resource/Brain'),
 ('areas', 'http://dbpedia.org/resource/Austin,_Texas'),
 ('acts', 'http://dbpedia.org/resource/Act_of_Parliament'),
 ('GHB receptor', 'http://dbpedia.org/resource/GHB_receptor'),
 ('weak', 'http://dbpedia.org/resource

In [11]:
#Test Setting with only 10 entities
#unique_entities = unique_entities[:500]

In [12]:
%%time

illegalDrugIndicators = [#'dbp:legalAu', # 'dbp:legalCa', 'dbp:legalDe', 'dbp:legalNz', 
                         #'dbp:legalUk',
    'dbp:legalUn', 'dbp:legalUs']

list_of_drugs = []
url = 'http://dbpedia.org/sparql'

#for ent_tuple in unique_entities:
for ent_tuple in tqdm(unique_entities):
    
    for ind in illegalDrugIndicators:
        query = """
                select * where {
                <""" + ent_tuple[1] + "> " + ind + " " + "?c" + """ }
                LIMIT 100
                """
        try:
            r = requests.get(url, params = {'format': 'json', 'query': query})
            data = r.json()

            if len(data['results']['bindings']) > 0:
                list_of_drugs.append(ent_tuple)
                break
        except Exception as e:
            print('Error ', e, ' at ', ent_tuple, ' and relation ', ind)
        
        

  6%|▌         | 8035/132626 [51:45<28:48:20,  1.20it/s]

Error  ('Connection aborted.', OSError(0, 'Error'))  at  ('rates', 'http://dbpedia.org/resource/Total_fertility_rate')  and relation  dbp:legalUn


  6%|▌         | 8038/132626 [54:35<1563:41:21, 45.18s/it]

Error  HTTPConnectionPool(host='dbpedia.org', port=80): Max retries exceeded with url: /sparql?format=json&query=%0A++++++++++++++++select+%2A+where+%7B%0A++++++++++++++++%3Chttp%3A%2F%2Fdbpedia.org%2Fresource%2FDemography%3E+dbp%3AlegalUs+%3Fc+%7D%0A++++++++++++++++LIMIT+100%0A++++++++++++++++ (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x7fb4a5ec2c18>: Failed to establish a new connection: [Errno 101] Network is unreachable',))  at  ('demographic', 'http://dbpedia.org/resource/Demography')  and relation  dbp:legalUs


 23%|██▎       | 31053/132626 [3:26:44<333:28:00, 11.82s/it]

...

Error  HTTPConnectionPool(host='dbpedia.org', port=80): Max retries exceeded with url: /sparql?format=json&query=%0A++++++++++++++++select+%2A+where+%7B%0A++++++++++++++++%3Chttp%3A%2F%2Fdbpedia.org%2Fresource%2FAnthony_McAuliffe%3E+dbp%3AlegalUn+%3Fc+%7D%0A++++++++++++++++LIMIT+100%0A++++++++++++++++ (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x7fb4a5ec2f98>: Failed to establish a new connection: [Errno 101] Network is unreachable',))  at  ('McAuliffe', 'http://dbpedia.org/resource/Anthony_McAuliffe')  and relation  dbp:legalUn


 96%|█████████▌| 127457/132626 [13:58:13<16:48:27, 11.71s/it] 

Error  ('Connection aborted.', OSError(0, 'Error'))  at  ('Hellenic', 'http://dbpedia.org/resource/Greece')  and relation  dbp:legalUs


100%|██████████| 132626/132626 [14:31:25<00:00,  2.54it/s]   

CPU times: user 2h 20min 49s, sys: 7min 47s, total: 2h 28min 36s
Wall time: 14h 31min 25s


In [13]:
#The resource link is unique and needs to be the identifier. Otherwise different writings linked to the known drug might be ignored..
drug_dict = {y:x for x,y in dict(list_of_drugs).items()}
drug_dict


{'http://dbpedia.org/resource/Gamma-Hydroxybutyric_acid': '4-Hydroxybutanoic acid',
 'http://dbpedia.org/resource/Lysergic_acid_diethylamide': 'flashback',
 'http://dbpedia.org/resource/Sodium_oxybate': 'Sodium oxybate',
 'http://dbpedia.org/resource/MDMA': 'xtc',
 'http://dbpedia.org/resource/Diazepam': 'valium',
 'http://dbpedia.org/resource/Baclofen': 'baclofen',
 'http://dbpedia.org/resource/Lorazepam': 'Ativan',
 'http://dbpedia.org/resource/Phenibut': 'Phenibut',
 'http://dbpedia.org/resource/Naloxone': 'suboxone',
 'http://dbpedia.org/resource/Naltrexone': 'buprenorphine/naltrexone',
 'http://dbpedia.org/resource/Chlordiazepoxide': 'Limbitrol',
 'http://dbpedia.org/resource/Pregabalin': 'Pregabalin',
 'http://dbpedia.org/resource/Alprazolam': 'xanax',
 'http://dbpedia.org/resource/Bromazepam': 'Bromazepam',
 'http://dbpedia.org/resource/Nitrazepam': 'Mogadon',
 'http://dbpedia.org/resource/Clonazepam': 'klonopin',
 'http://dbpedia.org/resource/Midazolam': 'Dormicum',
 'http://db

In [14]:
def label_drugs_in_text(entity_list, text, lookup_dict):
    final_text = text
    for candidate in entity_list:
        if candidate[1] in lookup_dict:
            final_text = final_text.replace(candidate[0], '<DRUG> '+candidate[0]+ ' </DRUG>')
    return final_text

def create_drug_label_list(entity_list, text, lookup_dict):
    labels = []
    for candidate in entity_list:
        if candidate[1] in lookup_dict:
            labels.append((candidate[0], 'Drug'))
    return labels
            

In [15]:
#df["newText"] = df.apply(lambda row: create_drug_label_list(row['entities'], row['text'], drug_dict2), axis=1)
df["labels"] = df.apply(lambda row: create_drug_label_list(row['entities'], row['text'], drug_dict), axis=1)

In [16]:
#Store raw
df.to_pickle('data/raw_annotated_DF_V1.2')

In [17]:
#Remove sentences without Drug label
index_to_del = df[ df['labels'].map(lambda d: len(d)) <= 0 ].index
df.drop(index_to_del, inplace=True)

In [18]:
#Store reduced Sentence set as Domain Text corpora
np.savetxt('data/reducedTextCorpusV1.2.txt', df["text"].values, fmt = "%s")

In [19]:
#Convert to BIO-NER task format
# Credits to Akash Chauhan - chauhanakash23.github.io

def matcher(string, pattern):
    '''
    Return the start and end index of any pattern present in the text.
    '''
    match_list = []
    pattern = pattern.strip()
    seqMatch = SequenceMatcher(None, string, pattern, autojunk=False)
    match = seqMatch.find_longest_match(0, len(string), 0, len(pattern))
    if (match.size == len(pattern)):
        start = match.a
        end = match.a + match.size
        match_tup = (start, end)
        string = string.replace(pattern, "X" * len(pattern), 1)
        match_list.append(match_tup)
        
    return match_list, string

def mark_sentence(s, match_list):
    '''
    Marks all the entities in the sentence as per the BIO scheme. 
    '''
    word_dict = {}
    for word in s.split():
        word_dict[word] = 'O'
        
    for start, end, e_type in match_list:
        temp_str = s[start:end]
        tmp_list = temp_str.split()
        if len(tmp_list) > 1:
            word_dict[tmp_list[0]] = 'B-' + e_type
            for w in tmp_list[1:]:
                word_dict[w] = 'I-' + e_type
        else:
            word_dict[temp_str] = 'B-' + e_type
    return word_dict

''' NOT NECESSARY SINCE CLEANING IS DONE ELSEWHERE
def clean(text):
    
    #Just a helper fuction to add a space before the punctuations for better tokenization
    filters = ["!", "#", "$", "%", "&", "(", ")", "/", "*", ".", ":", ";", "<", "=", ">", "?", "@", "[",
               "\\", "]", "_", "`", "{", "}", "~", "'"]
    for i in text:
        if i in filters:
            text = text.replace(i, " " + i)
            
    return text
'''

def create_data(df, filepath):
    '''
    The function responsible for the creation of data in the said format.
    '''
    with open(filepath , 'w') as f:
        for text, annotation in zip(df.text, df.annotation):
            #text = clean(text) # Cleaning need to be done in preprocessing
            text_ = text        
            match_list = []
            for i in annotation:
                a, text_ = matcher(text, i[0])
                match_list.append((a[0][0], a[0][1], i[1]))

            d = mark_sentence(text, match_list)

            for i in d.keys():
                f.writelines(i + ' ' + d[i] +'\n')
            f.writelines('\n')
            



In [20]:
## Subset and rename Train
bio_df = df[["text", "labels"]].copy()
bio_df.rename(columns = {'text':'text', 'labels':'annotation'}, inplace = True)


In [21]:
#Create and Store NER task file
full_filepath = 'data/bio_drugs_corpusV1.2.txt'
create_data(bio_df, full_filepath)

In [22]:
bio_df.shape

(37605, 2)

In [23]:
bio_train, bio_test = train_test_split(bio_df, test_size=0.1, random_state=42, shuffle=True)#10% --> 3900 rows should be enough
bio_train, bio_dev = train_test_split(bio_train, test_size=0.1, random_state=42, shuffle=True)

train_filepath = 'data/bio_drugs_corpus_trainV1.2.txt'
dev_filepath = 'data/bio_drugs_corpus_devV1.2.txt'
test_filepath = 'data/bio_drugs_corpus_testV1.2.txt'

create_data(bio_train, train_filepath)
create_data(bio_dev, dev_filepath)
create_data(bio_test, test_filepath)
